# confident_prediction_for_time_serial_indoor_temp_Keras

In [131]:
import os
import sys
import time
import optparse
import configparser
#import pyodbc
import pandas as pd
import numpy as np
import datetime
#import holidays
import re
from sklearn.preprocessing import MinMaxScaler, StandardScaler
import tensorflow as tf
from keras.callbacks import ModelCheckpoint
from keras.layers.core import Dense, Activation, Dropout
from keras.layers.recurrent import LSTM
from keras.layers import Input, concatenate, Lambda, Reshape, BatchNormalization, Dropout, Add
from keras.models import Sequential, Model

import scipy as sp
import scipy.stats
import matplotlib
import numpy as np
from matplotlib.pyplot import cm
import matplotlib.pyplot as plt
%matplotlib inline  
from ipywidgets import interact
from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.layouts import gridplot
from bokeh.models import HoverTool, ColumnDataSource, Band, Whisker
import ipywidgets as widgets
output_notebook()

Loading BokehJS ...

In [132]:
import tensorflow as tf
from keras.backend.tensorflow_backend import set_session
config = tf.ConfigProto()
#config.gpu_options.per_process_gpu_memory_fraction = 0.5
config.gpu_options.allow_growth=True
config.gpu_options.visible_device_list = "0"
set_session(tf.Session(config=config))


## Hyperparameter

In [133]:
T_out = 4 * 24
input_dim = 7
batch_size = 1 * 24 * 4 * 14
predictnet_epochs = 200
baseline_lstm_epochs = 50

is_load_predictnet_best_weight = True
is_load_baseline_lstm_best_weight = True
is_train_predictnet= False
is_train_baseline_lstm = False

predictnet_weight_filepath="./weights/lstm_dnn_with_ext.hdf5"
baseline_lstm_filepath="./weights/weights_baseline_lstm.best.hdf5"
df_param_file_path="./df_params.csv"

### DB Server Data Collection

> @TODO

### Local Data Collection

In [134]:
def time_process(date):
    time=datetime.datetime.strptime(date,'%Y-%m-%d %H:%M:%S.0000000')
    return datetime.datetime(time.year,time.month,time.day,time.hour)

def weather_data_feature_selected_and_serialize(df_weather):
    cols=['TempM','DewPointM','Humidity','WindSpeedM' ,'PressureM']
    for col in cols:
        df_weather = df_weather.loc[~(df_weather[col] == 'N/A')]
        df_weather = df_weather.loc[~(df_weather[col] == -9999)]
    date_trans=lambda date:datetime.datetime(date.year, date.month, date.day, date.hour)
    df_weather['time']=df_weather['Date'].apply(date_trans)
    df_weather = df_weather.dropna()
    df_weather.drop('Date',axis=1,inplace=True)
    result = df_weather.groupby('time').apply(np.mean)
    return result

def weather_data_interpolation(df_weather):
    interpolate_sample = df_weather.resample('15Min').asfreq()
    df_weather_interpolated = interpolate_sample.interpolate(method='time')
    return df_weather_interpolated

def space_temp_data_feature_selected_and_serialize(df_space):
    cols=['Date','temp', 'weekend', 'holiday']
    df_space = df_space[cols]
    df_space = df_space.dropna()
    date_trans=lambda date:datetime.datetime(date.year, date.month, date.day, date.hour, date.minute)
    df_space['time'] = df_space['Date'].apply(date_trans)
    df_space.drop('Date', axis=1, inplace=True)
    result = df_space.groupby('time').apply(np.mean)
    return result

def space_temp_extreme_data_clean_up(df_space, bad_values, verbose):
    df_space_cleaned = df_space.copy()
    
    clean_up_temp = []
    
    for bad_value in bad_values:
        for i in df_space.loc[df_space['temp'] == bad_value].index:
            clean_up_temp.append((df_space_cleaned.loc[i]))
            df_space_cleaned = df_space_cleaned.drop(i)
    
    if(verbose == True):
        show_interpolation_data_range(clean_up_temp)
    
    return df_space_cleaned

def space_temp_data_interpolation(df_space):
    interpolate_sample = df_space.resample('15Min').asfreq()
    df_space_interpolated = interpolate_sample.interpolate(method='time')
    return df_space_interpolated

def occupancy_data_serialize(df_occupancy):
    cols=['TIMESTAMP', 'VALUE']
    df_occupancy = df_occupancy[cols]
    df_occupancy = df_occupancy.dropna()
    date_trans=lambda date:datetime.datetime(date.year, date.month, date.day, date.hour, date.minute)
    df_occupancy['time'] = df_occupancy['TIMESTAMP'].apply(date_trans)
    df_occupancy['occupancy'] = df_occupancy['VALUE']
    df_occupancy.drop('TIMESTAMP', axis=1, inplace=True)
    df_occupancy.drop('VALUE', axis=1, inplace=True)
    result = df_occupancy.groupby('time').apply(np.mean)
    return df_occupancy

def occupancy_data_remove_duplicate(df_occupancy):
    df_occupancy = df_occupancy.copy()
    df_occupancy = df_occupancy[['TIMESTAMP', 'VALUE']]
    df_occupancy['date']=pd.to_datetime(df_occupancy['TIMESTAMP'])
    df_occupancy['occupancy']=df_occupancy['VALUE']
    df_occupancy.drop('TIMESTAMP', axis=1, inplace=True)
    df_occupancy.drop('VALUE', axis=1, inplace=True)
    df_occupancy = df_occupancy.set_index('date')
    df_occupancy_remove_duplicate = df_occupancy[~df_occupancy.index.duplicated()]
    return df_occupancy_remove_duplicate
    
def occupancy_data_interpolation(df_occupancy):
    for col in df_occupancy:
        df_occupancy[col] = pd.to_numeric(df_occupancy[col], errors='coerce')
    interpolate_sample = df_occupancy.resample('5Min').asfreq()
    df_occupancy_interpolated = interpolate_sample.interpolate(method='time')
    return df_occupancy_interpolated

def occupancy_data_duplicate_data(df_occupancy, year=1):
    df_occupancy = df_occupancy.copy()
    df_occupancy = df_occupancy.reset_index()
    year_index = 12 * 24 * 365 * year
    df_temp = pd.DataFrame(columns=['date','occupancy'])
    for i in range(year_index):
        length = len(df_occupancy)
        new_date = df_occupancy.loc[i, 'date'] -  pd.DateOffset(years=1)
        new_occupancy = df_occupancy.loc[i, 'occupancy']
        df_temp = df_temp.append({'date': new_date, 'occupancy': new_occupancy}, ignore_index=True)
        
    df_occupancy_duplicated = pd.concat([df_occupancy, df_temp]).set_index('date').sort_index() 
    return df_occupancy_duplicated

def occupancy_data_average_data(df_occupancy, year=1):
    df_occupancy = df_occupancy.copy()
    df_occupancy = df_occupancy.reset_index()
    year_index = 12 * 24 * 365 * year
    df_temp = pd.DataFrame(columns=['date','occupancy'])
    for i in range(year_index):
        length = len(df_occupancy)
        new_date = df_occupancy.loc[i, 'date'] -  pd.DateOffset(years=1)
        if(i + year_index < len(df_occupancy)):
            new_occupancy = (df_occupancy.loc[i, 'occupancy'] + df_occupancy.loc[i + year_index, 'occupancy']) / 2
        else:
            new_occupancy = df_occupancy.loc[i, 'occupancy']
        df_temp = df_temp.append({'date': new_date, 'occupancy': new_occupancy}, ignore_index=True)
        
    df_occupancy_duplicated = pd.concat([df_occupancy, df_temp]).set_index('date').sort_index() 
    return df_occupancy_duplicated

def data_resampling(dataframe, resample_rate=1):
    # resample every 1 row, i.e., do nothing
    if(resample_rate == 1):
        return dataframe
    else:
        return dataframe.iloc[::resample_rate, :]

# --------------- Preprocessing Delimiter ---------------------- #
def weather_data_preprocess(df_weather, bad_values=[0, 162.8, 250]):
    df_weather_serial = weather_data_feature_selected_and_serialize(df_weather)
    df_weather_serial_interpolated = weather_data_interpolation(df_weather_serial)    
    return df_weather_serial_interpolated
    
def space_temp_data_preprocess(df_space, bad_values=[0, 162.8, 250], verbose=False):
    df_space_serial = space_temp_data_feature_selected_and_serialize(df_space)
    df_space_serial_cleaned = space_temp_extreme_data_clean_up(df_space_serial, bad_values, verbose)
    df_space_serial_interpolated = space_temp_data_interpolation(df_space_serial_cleaned)
    
    return df_space_serial_interpolated

def occupancy_data_preprocess(df_occupancy, verbose=False):
    df_occupancy_remove_duplicate = occupancy_data_remove_duplicate(df_occupancy)
    df_occupancy_interpolated = occupancy_data_interpolation(df_occupancy_remove_duplicate)
    #df_occupancy_preprocessed = occupancy_data_duplicate_data(df_occupancy_interpolated)
    df_occupancy_preprocessed = occupancy_data_average_data(df_occupancy_interpolated)
    return df_occupancy_preprocessed

# In case people want to check the data after preprocessing
def write_data_to_excel(dataframe, filename):
    # Create a Pandas Excel writer using XlsxWriter as the engine.
    writer = pd.ExcelWriter(filename, engine='xlsxwriter')

    # Convert the dataframe to an XlsxWriter Excel object.
    dataframe.to_excel(writer, sheet_name='Sheet1')

    # Close the Pandas Excel writer and output the Excel file.
    writer.save()
    
# cleanning data printer
def show_interpolation_data_range(clean_up_list):
    bad_data_counter = {}
    
    for i, row in enumerate(clean_up_list):
        print(  'Temp: %s   '%(row['temp']), 'Date:', row.name)
        if(str(row['temp']) not in bad_data_counter):
            bad_data_counter[str(row['temp'])] = 1
        else:
            bad_data_counter[str(row['temp'])] += 1
    
    # Print counter
    for key, value in bad_data_counter.items():
        print('Clean up %s bad data(%s)' %(value, key))


In [135]:
try:
    df = pd.read_csv(df_param_file_path, index_col=0)
except Exception as e:
    print(e)
    assert False
    # read datas
    temp_space = pd.read_excel('./datasets/88688_gap_15min_space_temp_f18_csw.xlsx')
    temp_weather = pd.read_excel('./datasets/68364_gap_1h_weather_temp.xlsx')
    occupancy = pd.read_excel('./datasets/171553_gap_5min_occupancy.xlsx')

    # Preprocessing
    df_weather=pd.DataFrame(np.array(temp_weather),columns=['Run_DateTime','Date','UTC_Date','TempA','TempM',
                                                            'DewPointA','DewPointM' ,'Humidity' ,'WindSpeedA',
                                                           'WindSpeedM' ,'WindGustA' ,'WindGustM' ,'WindDir',
                                                           'VisibilityA' ,'VisibilityM' ,'PressureA' ,'PressureM',
                                                           'WindChillA' ,'WindChillM' ,'HeatIndexA' ,'HeatIndexM',
                                                           'PrecipA' ,'PrecipM' ,'Condition' ,'Fog' ,'Rain',
                                                           'Snow' ,'Hail' ,'Thunder','Tornado' ,'ID'])
    df_weather = df_weather[['Date','TempM','DewPointM','Humidity','WindSpeedM' ,'PressureM']]

    df_space = pd.DataFrame(np.array(temp_space),columns=['ID','zone','floor','quadrant','eq_no','Date','temp','weekend','holiday'])


    df_occupancy = pd.DataFrame(np.array(occupancy), columns=['ID', 'ZONE', 'FLOOR', 'QUADRANT', 'EQUIPMENT_NO', 'TIMESTAMP', 'VALUE'])


    df_weather_processed = weather_data_preprocess(df_weather)
    df_space_processed = space_temp_data_preprocess(df_space, bad_values=[0, 162.8, 250], verbose=False)
    df_occupancy_processed = occupancy_data_preprocess(df_occupancy, verbose=True)

    # Merge data
    df = pd.merge(df_weather_processed, df_space_processed, left_index=True, right_index=True)
    df = pd.merge(df, df_occupancy_processed, left_index=True, right_index=True)
    df.head()

    df.to_csv('df_params.csv')

In [136]:
scaler = StandardScaler()

def get_batch(df, batch_size=128, T=16, T_out = 24*4, input_dim=6, step=1, output_dim = 1, train=False):
    
    t = 0
    X_batch = np.empty(shape=[batch_size, T, input_dim])
    y_batch = np.empty(shape=[batch_size, T])
    labels = np.empty(shape=[batch_size, T_out, output_dim])
    #time_batch = np.empty(shape=[batch_size, T], dtype='datetime64')
    time_stamp_next_step = pd.to_datetime(df.index).tolist()
    time_stamp = np.array(pd.to_datetime(df.index)).reshape(len(time_stamp_next_step), 1)
    
    external_info = np.empty(shape=[batch_size, T_out, 2])
    next_step_time_batch = np.array([])
    next_24_hours_time_batch = np.empty(shape=[batch_size, T_out], dtype='datetime64[s]')
    
    X_all = scaler.fit_transform(df[['TempM', 'DewPointM','Humidity','WindSpeedM','PressureM','temp','occupancy']].values)
    Y_all = df["temp"].values
    Y_all = np.reshape(Y_all,(np.prod(Y_all.shape),1))
    Y_all = scaler.fit_transform(Y_all)
    ext = df[["weekend", "holiday"]].values
    for i in range(batch_size):
        X_batch[i,:,:] = X_all[t:t+T,:]
        y_batch[i,:] = Y_all[t:t+T,0]
        time_batch_all = time_stamp[t+T:t+T+T_out,0]
        l = Y_all[t+T:t+T+T_out,0]
        labels[i,:,:] = l.reshape((int(np.prod(l.shape)),1))
        external_info[i,:,:] = ext[t+T:t+T+T_out,0].reshape((int(np.prod(l.shape)),1))
        next_step_time_batch = np.append(next_step_time_batch, time_stamp_next_step[t+T])
        next_24_hours_time_batch[i, :] = time_batch_all
        t += step     
    
    # shuffle in train, not in test
        if train:
            index = list(range(batch_size))
            np.random.shuffle(index)
            X_batch = X_batch[index]
            y_batch = y_batch[index]
            labels = labels[index]
            external_info = external_info[index]
            next_step_time_batch = next_step_time_batch[index]
            next_24_hours_time_batch = next_24_hours_time_batch[index]

    return X_batch, y_batch, labels, next_step_time_batch, next_24_hours_time_batch, external_info

In [137]:
x, y, labels, next_step_time_info, next_24_hours_time_info, ext_info = get_batch(df, batch_size=int(T_out * int(len(df)/T_out)) - 8 * 24 * 4, T=7 * T_out, T_out=T_out, input_dim=input_dim)
train_samples = int(np.floor(x.shape[0] * 0.8))

In [138]:
print(x.shape)
print(y.shape)
print(labels.shape)
print(next_step_time_info.shape)
print(next_24_hours_time_info.shape)
print(ext_info.shape)

X_train = x[:train_samples,:,:]
X2_train = X_train[:,-T_out:,:]
Y_train = labels[:train_samples]
next_step_time_info_train = next_step_time_info[:train_samples]
next_24_hours_time_info_train = next_24_hours_time_info[:train_samples]
ext_train = ext_info[:train_samples]

X_test = x[train_samples:,:,:]
X2_test = X_test[:,-T_out:,:]
Y_test = labels[train_samples:]
next_step_time_info_test = next_step_time_info[train_samples:]
next_24_hours_time_info_test = next_24_hours_time_info[train_samples:]
ext_test = ext_info[train_samples:]

#Y_train = Y_train.reshape((Y_train.shape[0],Y_train.shape[1],1))
#Y_test = Y_test.reshape((Y_test.shape[0],Y_test.shape[1],1))
print(X_train.shape)
print(Y_train.shape)
print(X2_train.shape)
print(next_step_time_info_train.shape)
print(next_24_hours_time_info_train.shape)
print(ext_train.shape)
print(X_test.shape)
print(Y_test.shape)
print(X2_test.shape)
print(next_step_time_info_test.shape)
print(next_24_hours_time_info_test.shape)
print(ext_test.shape)

np.save('ground_true_time.npy', next_step_time_info_test)

(84768, 672, 7)
(84768, 672)
(84768, 96, 1)
(84768,)
(84768, 96)
(84768, 96, 2)
(67814, 672, 7)
(67814, 96, 1)
(67814, 96, 7)
(67814,)
(67814, 96)
(67814, 96, 2)
(16954, 672, 7)
(16954, 96, 1)
(16954, 96, 7)
(16954,)
(16954, 96)
(16954, 96, 2)


In [139]:
# Define an input sequence and process it.

encoder_inputs = Input(shape=(X_train.shape[1], X_train.shape[2]))
encoder = LSTM(64, return_sequences = True, dropout=0.2, recurrent_dropout=0.2)(encoder_inputs)
encoder_output, state_h, state_c = LSTM(64, return_sequences=True, return_state=True, dropout=0.2, recurrent_dropout=0.2)(encoder)

# We discard `encoder_outputs` and only keep the states.
encoder_states = concatenate([state_h, state_c])
#pred_latent = 64
dense_prediction = Dense(Y_train.shape[1] * 96, activation = 'relu')(encoder_states)
dense_prediction = Dense(Y_train.shape[1] * 48, activation = 'relu')(encoder_states)
dense_prediction = Dense(Y_train.shape[1] * 16, activation = 'relu')(dense_prediction)
dense_prediction = Dense(Y_train.shape[1] * 8, activation = 'relu')(dense_prediction)
dense_prediction = Dense(Y_train.shape[1] * 4, activation = 'relu')(dense_prediction)
dense_prediction = Dense(Y_train.shape[1] * 2, activation = 'relu')(dense_prediction)
dense_prediction = Dense(Y_train.shape[1] * Y_train.shape[2], activation = 'linear')(dense_prediction)

ext_inputs = Input(shape=(ext_train.shape[1], ext_train.shape[2]))
ext_embedding = Reshape((ext_train.shape[1]*ext_train.shape[2],))(ext_inputs)
ext_embedding = Dense(ext_train.shape[1]*ext_train.shape[2], activation='relu')(ext_embedding)
ext_prediction = Dense(Y_train.shape[1] * Y_train.shape[2], activation='linear')(ext_embedding)
all_prediction = Add()([dense_prediction, ext_prediction])
#all_prediction = Dense(Y_train.shape[1] * Y_train.shape[2], activation='tanh')(all_prediction)
all_prediction = Dropout(0.1)(all_prediction, training=True)
all_prediction = Reshape((Y_train.shape[1], Y_train.shape[2]), name = 'prediction_output')(all_prediction)

#Dense(n_embedding)(encoder_states)

model = Model([encoder_inputs, ext_inputs], [all_prediction])
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 672, 7)       0                                            
__________________________________________________________________________________________________
lstm_1 (LSTM)                   (None, 672, 64)      18432       input_1[0][0]                    
__________________________________________________________________________________________________
lstm_2 (LSTM)                   [(None, 672, 64), (N 33024       lstm_1[0][0]                     
__________________________________________________________________________________________________
concatenate_1 (Concatenate)     (None, 128)          0           lstm_2[0][1]                     
                                                                 lstm_2[0][2]                     
__________

### Predict Net - Model Training

In [140]:
import keras.backend as K
def customLoss(y_true, y_pred):
    loss = K.mean(( (abs(y_pred - y_true) ** 2)), axis=-1)
    #loss = K.mean(K.pow(K.pow(abs(y_pred - y_true), 3), 0.33), axis=-1)
    #loss = K.mean(K.sqrt(K.pow((y_pred - y_true), 2), axis=-1)  RMSE
    return loss

In [141]:
# Run training
model.compile(optimizer='adam', loss=customLoss)
              #loss={'prediction_output': customLoss},
              #loss_weights={'prediction_output': 1.0})

if(is_load_predictnet_best_weight is True):
    model.load_weights(predictnet_weight_filepath)

if(is_train_predictnet is True):
    checkpoint = ModelCheckpoint(predictnet_weight_filepath, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
    callbacks_list = [checkpoint]
    
    print('Starting training...')
    model.fit([X_train, ext_train], [Y_train],
              batch_size=batch_size,
              epochs=predictnet_epochs,
              validation_split=0.2,
              callbacks=callbacks_list)

In [142]:
Y_test_p = np.load('ground_true.npy')
Y_preds_predictnet = np.load('lstm_dnn_with_ext.npy')
y_68_min_confident_interval = np.load('lstm_dnn_with_ext_68_min_confident_interval.npy')
y_68_max_confident_interval = np.load('lstm_dnn_with_ext_68_max_confident_interval.npy')
y_95_min_confident_interval = np.load('lstm_dnn_with_ext_95_min_confident_interval.npy')
y_95_max_confident_interval = np.load('lstm_dnn_with_ext_95_max_confident_interval.npy')
y_preds_avg =  (y_68_min_confident_interval + y_68_max_confident_interval) / 2


Y_preds_predictnet_no_ext = np.load('lstm_dnn.npy')
y_68_min_confident_interval_no_ext = np.load('lstm_dnn_68_min_confident_interval.npy')
y_68_max_confident_interval_no_ext = np.load('lstm_dnn_68_max_confident_interval.npy')
y_95_min_confident_interval_no_ext = np.load('lstm_dnn_95_min_confident_interval.npy')
y_95_max_confident_interval_no_ext = np.load('lstm_dnn_95_max_confident_interval.npy')
y_preds_avg_no_ext =  (y_68_min_confident_interval_no_ext + y_68_max_confident_interval_no_ext) / 2

In [143]:
dd = pd.DataFrame(list(Y_test_p[:,0,0]))

In [144]:
dd.to_csv('true_weathe.csv')

### Predict Net - Next Step Predition

In [145]:
next_step_source_gt = ColumnDataSource(data=dict(x=next_step_time_info_test, y=Y_test_p[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test]))
next_step_source_pred = ColumnDataSource(data=dict(x=next_step_time_info_test, y=Y_preds_predictnet[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test], y_95_min=y_95_min_confident_interval[:,0,0], y_95_max=y_95_max_confident_interval[:,0,0], y_68_min=y_68_min_confident_interval[:,0,0], y_68_max=y_68_max_confident_interval[:,0,0]))
TOOLS="crosshair,pan,wheel_zoom,xwheel_zoom,reset,tap"
p=figure(title="Next Step Floor Temperature Prediction", plot_height=600, plot_width=900, x_axis_type='datetime', tools=TOOLS)
hover = HoverTool(tooltips=None, mode="vline")
p.add_tools(HoverTool(tooltips = [('Temp', '@y'), 
                                  ('Date', '@date_str')], mode="vline"))
p.line('x', 'y', color='black', line_width=3, source=next_step_source_gt)

p.line('x', 'y', color='blue', line_width=3, source=next_step_source_pred)
#band_95 = Band(base='x', lower='y_95_min', upper='y_95_max', source=next_step_source_pred, level='underlay',
#               fill_color = 'green', fill_alpha=0.3, line_width=2, line_color='black')
#band_68 = Band(base='x', lower='y_68_min', upper='y_68_max', source=next_step_source_pred, level='underlay',
#               fill_color = 'yellow', fill_alpha=0.3, line_width=3, line_color='red')
#p.add_layout(band_68)
#p.add_layout(band_95)

p.xgrid.grid_line_color = None
p.legend.orientation = "horizontal"
p.legend.location = "top_center"
show(p)

print("PredictNet RMSE : ", np.sum((Y_preds_predictnet[:, 0, :] - Y_test_p[:, 0, :]) ** 2) / len(Y_test_p[:, 0, :]))
print("PredictNet MAE : ", np.sum(abs(Y_preds_predictnet[:, 0, :] - Y_test_p[:, 0, :])) / len(Y_test_p[:, 0, :]))
print("PredictNet MAPE : ", np.sum(abs((Y_preds_predictnet[:, 0, :] - Y_test_p[:, 0, :]) / Y_test_p[:, 0, :])) / len(Y_test_p[:, 0, :]) * 100)

total_max_pred_rmse = 0
total_max_pred_mae = 0
total_max_pred_mape = 0
total_min_pred_rmse = 0
total_min_pred_mae = 0
total_min_pred_mape = 0
counter = 0
for i in range(0, len(Y_preds_predictnet), 24):
    max_index = i + np.argmax((Y_preds_predictnet[i:i+23, 0, :]))
    min_index = i + np.argmin((Y_preds_predictnet[i:i+23, 0, :]))
    if(max_index <= 2):
        max_index = 2
    if(min_index <= 2):
        min_index = 2
    
    counter += 1
    total_max_pred_rmse += np.sum((Y_preds_predictnet[max_index-2:max_index+2, 0, :] - Y_test_p[max_index-2:max_index+2, 0, :]) ** 2) / len(Y_test_p[max_index-2:max_index+2, 0, :])
    total_max_pred_mae += np.sum(abs(Y_preds_predictnet[max_index-2:max_index+2, 0, :] - Y_test_p[max_index-2:max_index+2, 0, :])) / len(Y_test_p[max_index-2:max_index+2, 0, :])
    total_max_pred_mape += np.sum(abs((Y_preds_predictnet[max_index-2:max_index+2, 0, :] - Y_test_p[max_index-2:max_index+2, 0, :]) / Y_test_p[max_index-2:max_index+2, 0, :])) / len(Y_test_p[max_index-2:max_index+2, 0, :]) * 100
    
    total_min_pred_rmse += np.sum((Y_preds_predictnet[min_index-2:min_index+2, 0, :] - Y_test_p[min_index-2:min_index+2, 0, :]) ** 2) / len(Y_test_p[min_index-2:min_index+2, 0, :])
    total_min_pred_mae += np.sum(abs(Y_preds_predictnet[min_index-2:min_index+2, 0, :] - Y_test_p[min_index-2:min_index+2, 0, :])) / len(Y_test_p[min_index-2:min_index+2, 0, :])
    total_min_pred_mape += np.sum(abs((Y_preds_predictnet[min_index-2:min_index+2, 0, :] - Y_test_p[min_index-2:min_index+2, 0, :]) / Y_test_p[min_index-2:min_index+2, 0, :])) / len(Y_test_p[min_index-2:min_index+2, 0, :]) * 100
    
print("Max PredictNet RMSE : %f" %(total_max_pred_rmse / counter))
print("Max PredictNet MAE : %f" %(total_max_pred_mae / counter))
print("Max PredictNet MAPE : %f" %(total_max_pred_mape / counter))
print("Min PredictNet RMSE : %f" %(total_min_pred_rmse / counter))
print("Min PredictNet MAE : %f" %(total_min_pred_mae / counter))
print("Min PredictNet MAPE : %f" %(total_min_pred_mape / counter))

counter_68 = 0
counter_95 = 0
for i in range(0, len(Y_preds_predictnet)):
    if((Y_test_p[i,0,0] < y_95_min_confident_interval[i,0,0]) or (Y_test_p[i,0,0] > y_95_max_confident_interval[i,0,0])):
        counter_95 += 1
    if((Y_test_p[i,0,0] < y_68_min_confident_interval[i,0,0]) or (Y_test_p[i,0,0] > y_68_max_confident_interval[i,0,0])):
        counter_68 += 1

print("Exceeds 68%% Confidence Probability: %f%%" %(counter_68 / len(Y_test_p)*100))
print("Exceeds 95%% Confidence Probability: %f%%" %(counter_95 / len(Y_test_p)*100))

C:\Users\zd2212\AppData\Local\conda\conda\envs\tflatest\lib\site-packages\bokeh\plotting\helpers.py:535: UserWarning: WheelZoomTool are being repeated
  warnings.warn("%s are being repeated" % ",".join(repeated_tools))


PredictNet RMSE :  0.6926026469646454
PredictNet MAE :  0.5350886407217822
PredictNet MAPE :  0.6973075573403879
Max PredictNet RMSE : 0.878297
Max PredictNet MAE : 0.602558
Max PredictNet MAPE : 0.780117
Min PredictNet RMSE : 1.051339
Min PredictNet MAE : 0.625132
Min PredictNet MAPE : 0.815105
Exceeds 68% Confidence Probability: 38.781409%
Exceeds 95% Confidence Probability: 16.733514%


In [159]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, CDSView, GroupFilter
from bokeh.sampledata.iris import flowers

source = ColumnDataSource(flowers)

setosa = CDSView(source=source, filters=[GroupFilter(column_name='species', group='setosa')])
versicolor = CDSView(source=source, filters=[GroupFilter(column_name='species', group='versicolor')])
virginica = CDSView(source=source, filters=[GroupFilter(column_name='species', group='virginica')])

p = figure()

p.circle(x='petal_length', y='petal_width', source=source, view=setosa,
         size=10, color='red', alpha=0.6, legend='setosa')

p.square(x='petal_length', y='petal_width', source=source, view=versicolor,
         size=10, color='green', alpha=0.6, legend='versicolor')

p.triangle(x='petal_length', y='petal_width', source=source, view=virginica,
           size=10, color='blue', alpha=0.6, legend='virginica')

p.legend.location = "top_left"
show(p)

In [171]:

from bokeh.models.markers import Triangle
next_step_source_gt = ColumnDataSource(data=dict(x=next_step_time_info_test, y=Y_test_p[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test]))
next_step_source_pred = ColumnDataSource(data=dict(x=next_step_time_info_test, y=y_preds_avg[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test], y_95_min=y_95_min_confident_interval[:,0,0], y_95_max=y_95_max_confident_interval[:,0,0], y_68_min=y_68_min_confident_interval[:,0,0], y_68_max=y_68_max_confident_interval[:,0,0]))
next_step_source_pred_no_ext = ColumnDataSource(data=dict(x=next_step_time_info_test, y=y_preds_avg_no_ext[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test], y_95_min=y_95_min_confident_interval_no_ext[:,0,0], y_95_max=y_95_max_confident_interval_no_ext[:,0,0], y_68_min=y_68_min_confident_interval_no_ext[:,0,0], y_68_max=y_68_max_confident_interval_no_ext[:,0,0]))

TOOLS="crosshair,xpan,wheel_zoom,xwheel_zoom,reset,tap,save"
p=figure(title="Indoor Floor Temperature Prediction", plot_height=600, plot_width=2100, x_axis_type='datetime', tools=TOOLS)
hover = HoverTool(tooltips=None, mode="vline")
p.add_tools(HoverTool(tooltips = [('Temp', '@y'), 
                                  ('Date', '@date_str')], mode="vline"))
p.line('x', 'y', color='black', line_width=3, source=next_step_source_gt, legend='ground truth')
p.line('x', 'y', color='lightgray', line_dash="dashed",  line_width=3, source=next_step_source_pred_no_ext, legend='prediction of LSTM-DNN')
p.line(x="x", y="y", color='gray', line_dash="dashed",  line_width=3, source=next_step_source_pred, legend='prediction of LSTM-DNN (adjoint)')
# band_95 = Band(base='x', lower='y_95_min', upper='y_95_max', source=next_step_source_pred, level='underlay',
#               fill_color = 'lightgrey', fill_alpha=0.5, line_width=2, line_color='lightgrey')
# band_68 = Band(base='x', lower='y_68_min', upper='y_68_max', source=next_step_source_pred, level='underlay',
#               fill_color = 'grey', fill_alpha=0.8, line_width=3, line_color='grey')
# p.add_layout(band_68)
# p.add_layout(band_95)


p.xgrid.grid_line_color = None
p.yaxis.axis_label = 'Temperature (Fahrenheit)'
p.legend.orientation = "vertical"
p.legend.location = "top_left"
p.legend.background_fill_alpha = 0.5
p.legend.label_text_font_size = "14pt"
p.xaxis.axis_label_text_font_size = "14pt"
p.yaxis.axis_label_text_font_size = "14pt"
p.xaxis.major_label_text_font_size = "14pt"
p.yaxis.major_label_text_font_size = "14pt"
p.xaxis.axis_label_text_font_style = 'normal'
p.yaxis.axis_label_text_font_style = 'normal'
show(p)

C:\Users\zd2212\AppData\Local\conda\conda\envs\tflatest\lib\site-packages\bokeh\plotting\helpers.py:535: UserWarning: WheelZoomTool are being repeated
  warnings.warn("%s are being repeated" % ",".join(repeated_tools))


### Predict Net - Next 24 Hours Predition

In [172]:
all_plots = []
import random

i = 887
#i_list = [i + step for step in range(96)]
i_list = [i+96*j for j in [17, 18, 29, 30,31, 45,46, 63, 107,108]]
for index, i in enumerate(i_list[::1]):    
    next_24hours_source_gt = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=Y_test_p[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]]))
    next_24hours_source_pred = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=y_preds_avg[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]], y_95_min=y_95_min_confident_interval[i,:], y_95_max=y_95_max_confident_interval[i,:], y_68_min=y_68_min_confident_interval[i,:], y_68_max=y_68_max_confident_interval[i,:]))
    next_step_source_pred_no_ext = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=y_preds_avg_no_ext[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]], y_95_min=y_95_min_confident_interval_no_ext[i,:], y_95_max=y_95_max_confident_interval_no_ext[i,:], y_68_min=y_68_min_confident_interval_no_ext[i,:], y_68_max=y_68_max_confident_interval_no_ext[i,:]))

    TOOLS="crosshair,pan,wheel_zoom,xwheel_zoom,reset,tap, save"
    p=figure(title="24 Hours Floor Temperature Prediction: %s"%(next_24_hours_time_info_test[i,0].astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S")), x_axis_type='datetime', tools=TOOLS)
    hover = HoverTool(tooltips=None, mode="vline")
    p.add_tools(HoverTool(tooltips = [('Temp', '@y'), 
                                      ('Date', '@date_str')], mode="vline"))
    gt = p.line('x', 'y', color='black', line_width=3, source=next_24hours_source_gt,  legend='ground truth')
    pred_no_ext = p.line('x', 'y', color='lightgray', line_width=3, line_dash="dashed",  source=next_step_source_pred_no_ext, legend='prediction of LSTM-DNN')
    pred = p.line('x', 'y', color='gray', line_width=3, line_dash="dashed",  source=next_24hours_source_pred, legend='prediction of LSTM-DNN (adjoint)')
    
    #band_95 = Band(base='x', lower='y_95_min', upper='y_95_max', source=next_24hours_source_pred, level='underlay',
    #               fill_color = 'green', fill_alpha=0.3, line_width=2, line_color='black')
    #band_68 = Band(base='x', lower='y_68_min', upper='y_68_max', source=next_24hours_source_pred, level='underlay',
    #               fill_color = 'yellow', fill_alpha=0.3, line_width=3, line_color='red')
    # p.add_layout(band_68)
    # p.add_layout(band_95)
    p.xgrid.grid_line_color = None
    p.yaxis.axis_label = 'Temperature (Fahrenheit)'
    p.legend.orientation = "vertical"
    p.legend.location = "top_center"
    p.legend.background_fill_alpha = 0.5
    p.legend.label_text_font_size = "14pt"
    p.xaxis.axis_label_text_font_size = "14pt"
    p.yaxis.axis_label_text_font_size = "14pt"
    p.xaxis.major_label_text_font_size = "14pt"
    p.yaxis.major_label_text_font_size = "14pt"
    p.xaxis.axis_label_text_font_style = 'normal'
    p.yaxis.axis_label_text_font_style = 'normal'
    all_plots.append(p)

grid = gridplot(all_plots, ncols=1, plot_width=950, plot_height=380)

show(grid)

print("PredictNet RMSE : ", np.sum((Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :]) ** 2) / (Y_test_p.shape[0] * Y_test_p.shape[1]))
print("PredictNet MAE : ", np.sum(abs(Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :])) / (Y_test_p.shape[0] * Y_test_p.shape[1]))
print("PredictNet MAPE : ", np.sum(abs((Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :]) / Y_test_p[:, :, :])) / (Y_test_p.shape[0] * Y_test_p.shape[1]) * 100)


total_max_pred_rmse = 0
total_max_pred_mae = 0
total_max_pred_mape = 0
total_min_pred_rmse = 0
total_min_pred_mae = 0
total_min_pred_mape = 0
counter = 0
for i in range(0, len(Y_preds_predictnet)):
    max_index = i + np.argmax((Y_preds_predictnet[i, :, :]))
    min_index = i + np.argmin((Y_preds_predictnet[i, :, :]))
    if(max_index <= 2):
        max_index = 2
    if(min_index <= 2):
        min_index = 2
    if(max_index >= 22):
        max_index = 22
    if(min_index >= 22):
        min_index = 22
    
    counter += 1
    total_max_pred_rmse += np.sum((Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :]) ** 2) / len(Y_test_p[i, max_index-2:max_index+2, :])
    total_max_pred_mae += np.sum(abs(Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :])) / len(Y_test_p[i, max_index-2:max_index+2, :])
    total_max_pred_mape += np.sum(abs((Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :]) / Y_test_p[i, max_index-2:max_index+2, :])) / len(Y_test_p[i, max_index-2:max_index+2, :]) * 100
    
    total_min_pred_rmse += np.sum((Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :]) ** 2) / len(Y_test_p[i, min_index-2:min_index+2, :])
    total_min_pred_mae += np.sum(abs(Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :])) / len(Y_test_p[i, min_index-2:min_index+2, :])
    total_min_pred_mape += np.sum(abs((Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :]) / Y_test_p[i, min_index-2:min_index+2, :])) / len(Y_test_p[i, min_index-2:min_index+2, :]) * 100

print("Max PredictNet RMSE : %f" %(total_max_pred_rmse / counter))
print("Max PredictNet MAE : %f" %(total_max_pred_mae / counter))
print("Max PredictNet MAPE : %f" %(total_max_pred_mape / counter))
print("Min PredictNet RMSE : %f" %(total_min_pred_rmse / counter))
print("Min PredictNet MAE : %f" %(total_min_pred_mae / counter))
print("Min PredictNet MAPE : %f" %(total_min_pred_mape / counter))

counter_68 = 0
counter_95 = 0
for i in range(0, len(Y_preds_predictnet)):
    for j in range(0, 24):
        if((Y_test_p[i,j,0] < y_95_min_confident_interval[i,j,0]) or (Y_test_p[i,j,0] > y_95_max_confident_interval[i,j,0])):
            counter_95 += 1
        if((Y_test_p[i,j,0] < y_68_min_confident_interval[i,j,0]) or (Y_test_p[i,j,0] > y_68_max_confident_interval[i,j,0])):
            counter_68 += 1

print("Exceeds 68%% Confidence Probability: %f%%" %(counter_68 / len(Y_test_p) / len(Y_test_p[0])*100))
print("Exceeds 95%% Confidence Probability: %f%%" %(counter_95 / len(Y_test_p) / len(Y_test_p[0])*100))

C:\Users\zd2212\AppData\Local\conda\conda\envs\tflatest\lib\site-packages\bokeh\plotting\helpers.py:535: UserWarning: WheelZoomTool are being repeated
  warnings.warn("%s are being repeated" % ",".join(repeated_tools))


PredictNet RMSE :  1.6797635806980036
PredictNet MAE :  0.922831946997324
PredictNet MAPE :  1.2023872079127942
Max PredictNet RMSE : 1.461522
Max PredictNet MAE : 0.869743
Max PredictNet MAPE : 1.134757
Min PredictNet RMSE : 1.461500
Min PredictNet MAE : 0.869683
Min PredictNet MAPE : 1.134682
Exceeds 68% Confidence Probability: 13.252342%
Exceeds 95% Confidence Probability: 8.094882%


In [174]:
next_step_source_gt = ColumnDataSource(data=dict(x=next_step_time_info_test, y=Y_test_p[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test]))
next_step_source_pred = ColumnDataSource(data=dict(x=next_step_time_info_test, y=y_preds_avg[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test], y_95_min=y_95_min_confident_interval[:,0,0], y_95_max=y_95_max_confident_interval[:,0,0], y_68_min=y_68_min_confident_interval[:,0,0], y_68_max=y_68_max_confident_interval[:,0,0]))
next_step_source_pred_no_ext = ColumnDataSource(data=dict(x=next_step_time_info_test, y=y_preds_avg_no_ext[:, 0, 0], date_str=[x.strftime("%Y-%m-%d %H:%M:%S") for x in next_step_time_info_test], y_95_min=y_95_min_confident_interval_no_ext[:,0,0], y_95_max=y_95_max_confident_interval_no_ext[:,0,0], y_68_min=y_68_min_confident_interval_no_ext[:,0,0], y_68_max=y_68_max_confident_interval_no_ext[:,0,0]))

TOOLS="crosshair,xpan,wheel_zoom,xwheel_zoom,reset,tap,save"
p=figure(title="Indoor Floor Temperature Prediction", plot_height=600, plot_width=2100, x_axis_type='datetime', tools=TOOLS)
hover = HoverTool(tooltips=None, mode="vline")
p.add_tools(HoverTool(tooltips = [('Temp', '@y'), 
                                  ('Date', '@date_str')], mode="vline"))
p.line('x', 'y', color='black', line_width=3, source=next_step_source_gt, legend='ground truth')
#p.line('x', 'y', color='green', line_width=3, source=next_step_source_pred_no_ext, legend='prediction of LSTM-DNN')
p.line('x', 'y', color='#333333', line_width=3, line_dash="dashed",  source=next_step_source_pred, legend='prediction of LSTM-DNN (adjoint)')
band_95 = Band(base='x', lower='y_95_min', upper='y_95_max', source=next_step_source_pred, level='underlay',
               fill_color = '#808080', fill_alpha=0.6, line_width=2, line_color='lightgrey')
band_68 = Band(base='x', lower='y_68_min', upper='y_68_max', source=next_step_source_pred, level='underlay',
               fill_color = '#595959', fill_alpha=0.8, line_width=3, line_color='grey')
p.add_layout(band_68)
p.add_layout(band_95)


p.xgrid.grid_line_color = None
p.yaxis.axis_label = 'Temperature (Fahrenheit)'
p.legend.orientation = "vertical"
p.legend.location = "top_left"
p.legend.background_fill_alpha = 0.5
p.legend.label_text_font_size = "14pt"
p.xaxis.axis_label_text_font_size = "14pt"
p.yaxis.axis_label_text_font_size = "14pt"
p.xaxis.major_label_text_font_size = "14pt"
p.yaxis.major_label_text_font_size = "14pt"
p.xaxis.axis_label_text_font_style = 'normal'
p.yaxis.axis_label_text_font_style = 'normal'
show(p)

C:\Users\zd2212\AppData\Local\conda\conda\envs\tflatest\lib\site-packages\bokeh\plotting\helpers.py:535: UserWarning: WheelZoomTool are being repeated
  warnings.warn("%s are being repeated" % ",".join(repeated_tools))


In [177]:
all_plots = []
import random

i = 887
#i_list = [i + step for step in range(96)]
i_list = [i+96*j for j in [17, 18, 29, 30,31, 45,46, 63, 107,108]]
for index, i in enumerate(i_list[::1]):    
    next_24hours_source_gt = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=Y_test_p[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]]))
    next_24hours_source_pred = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=y_preds_avg[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]], y_95_min=y_95_min_confident_interval[i,:], y_95_max=y_95_max_confident_interval[i,:], y_68_min=y_68_min_confident_interval[i,:], y_68_max=y_68_max_confident_interval[i,:]))
    next_step_source_pred_no_ext = ColumnDataSource(data=dict(x=next_24_hours_time_info_test[i,:], y=y_preds_avg_no_ext[i, :], date_str=[x.astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S") for x in next_24_hours_time_info_test[i,:]], y_95_min=y_95_min_confident_interval_no_ext[i,:], y_95_max=y_95_max_confident_interval_no_ext[i,:], y_68_min=y_68_min_confident_interval_no_ext[i,:], y_68_max=y_68_max_confident_interval_no_ext[i,:]))

    TOOLS="crosshair,xpan,wheel_zoom,xwheel_zoom,reset,tap, save"
    p=figure(title="24 Hours Floor Temperature Prediction: %s"%(next_24_hours_time_info_test[i,0].astype(datetime.datetime).strftime("%Y-%m-%d %H:%M:%S")), x_axis_type='datetime', tools=TOOLS)
    hover = HoverTool(tooltips=None, mode="vline")
    p.add_tools(HoverTool(tooltips = [('Temp', '@y'), 
                                      ('Date', '@date_str')], mode="vline"))
    gt = p.line('x', 'y', color='black', line_width=3, source=next_24hours_source_gt,  legend='ground truth')
    #pred_no_ext = p.line('x', 'y', color='green', line_width=3, source=next_step_source_pred_no_ext, legend='prediction of LSTM-DNN')
    pred = p.line('x', 'y', color='#333333', line_width=3, line_dash="dashed", source=next_24hours_source_pred, legend='prediction of LSTM-DNN (adjoint)')
    
    band_95 = Band(base='x', lower='y_95_min', upper='y_95_max', source=next_24hours_source_pred, level='underlay',
              fill_color = '#808080', fill_alpha=0.6, line_width=4, line_color='lightgrey')
    band_68 = Band(base='x', lower='y_68_min', upper='y_68_max', source=next_24hours_source_pred, level='underlay',
              fill_color = '#595959', fill_alpha=0.8, line_width=4, line_color='grey')
    p.add_layout(band_68)
    p.add_layout(band_95)
    p.xgrid.grid_line_color = None
    p.yaxis.axis_label = 'Temperature (Fahrenheit)'
    p.legend.orientation = "vertical"
    p.legend.location = "top_center"
    p.legend.background_fill_alpha = 0.5
    p.legend.label_text_font_size = "14pt"
    p.xaxis.axis_label_text_font_size = "14pt"
    p.yaxis.axis_label_text_font_size = "14pt"
    p.xaxis.major_label_text_font_size = "14pt"
    p.yaxis.major_label_text_font_size = "14pt"
    p.xaxis.axis_label_text_font_style = 'normal'
    p.yaxis.axis_label_text_font_style = 'normal'
    all_plots.append(p)

grid = gridplot(all_plots, ncols=1, plot_width=950, plot_height=380)

show(grid)

print("PredictNet RMSE : ", np.sum((Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :]) ** 2) / (Y_test_p.shape[0] * Y_test_p.shape[1]))
print("PredictNet MAE : ", np.sum(abs(Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :])) / (Y_test_p.shape[0] * Y_test_p.shape[1]))
print("PredictNet MAPE : ", np.sum(abs((Y_preds_predictnet[:, :, :] - Y_test_p[:, :, :]) / Y_test_p[:, :, :])) / (Y_test_p.shape[0] * Y_test_p.shape[1]) * 100)


total_max_pred_rmse = 0
total_max_pred_mae = 0
total_max_pred_mape = 0
total_min_pred_rmse = 0
total_min_pred_mae = 0
total_min_pred_mape = 0
counter = 0
for i in range(0, len(Y_preds_predictnet)):
    max_index = i + np.argmax((Y_preds_predictnet[i, :, :]))
    min_index = i + np.argmin((Y_preds_predictnet[i, :, :]))
    if(max_index <= 2):
        max_index = 2
    if(min_index <= 2):
        min_index = 2
    if(max_index >= 22):
        max_index = 22
    if(min_index >= 22):
        min_index = 22
    
    counter += 1
    total_max_pred_rmse += np.sum((Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :]) ** 2) / len(Y_test_p[i, max_index-2:max_index+2, :])
    total_max_pred_mae += np.sum(abs(Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :])) / len(Y_test_p[i, max_index-2:max_index+2, :])
    total_max_pred_mape += np.sum(abs((Y_preds_predictnet[i, max_index-2:max_index+2, :] - Y_test_p[i, max_index-2:max_index+2, :]) / Y_test_p[i, max_index-2:max_index+2, :])) / len(Y_test_p[i, max_index-2:max_index+2, :]) * 100
    
    total_min_pred_rmse += np.sum((Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :]) ** 2) / len(Y_test_p[i, min_index-2:min_index+2, :])
    total_min_pred_mae += np.sum(abs(Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :])) / len(Y_test_p[i, min_index-2:min_index+2, :])
    total_min_pred_mape += np.sum(abs((Y_preds_predictnet[i, min_index-2:min_index+2, :] - Y_test_p[i, min_index-2:min_index+2, :]) / Y_test_p[i, min_index-2:min_index+2, :])) / len(Y_test_p[i, min_index-2:min_index+2, :]) * 100

print("Max PredictNet RMSE : %f" %(total_max_pred_rmse / counter))
print("Max PredictNet MAE : %f" %(total_max_pred_mae / counter))
print("Max PredictNet MAPE : %f" %(total_max_pred_mape / counter))
print("Min PredictNet RMSE : %f" %(total_min_pred_rmse / counter))
print("Min PredictNet MAE : %f" %(total_min_pred_mae / counter))
print("Min PredictNet MAPE : %f" %(total_min_pred_mape / counter))

counter_68 = 0
counter_95 = 0
for i in range(0, len(Y_preds_predictnet)):
    for j in range(0, 24):
        if((Y_test_p[i,j,0] < y_95_min_confident_interval[i,j,0]) or (Y_test_p[i,j,0] > y_95_max_confident_interval[i,j,0])):
            counter_95 += 1
        if((Y_test_p[i,j,0] < y_68_min_confident_interval[i,j,0]) or (Y_test_p[i,j,0] > y_68_max_confident_interval[i,j,0])):
            counter_68 += 1

print("Exceeds 68%% Confidence Probability: %f%%" %(counter_68 / len(Y_test_p) / len(Y_test_p[0])*100))
print("Exceeds 95%% Confidence Probability: %f%%" %(counter_95 / len(Y_test_p) / len(Y_test_p[0])*100))

C:\Users\zd2212\AppData\Local\conda\conda\envs\tflatest\lib\site-packages\bokeh\plotting\helpers.py:535: UserWarning: WheelZoomTool are being repeated
  warnings.warn("%s are being repeated" % ",".join(repeated_tools))


PredictNet RMSE :  1.6797635806980036
PredictNet MAE :  0.922831946997324
PredictNet MAPE :  1.2023872079127942
Max PredictNet RMSE : 1.461522
Max PredictNet MAE : 0.869743
Max PredictNet MAPE : 1.134757
Min PredictNet RMSE : 1.461500
Min PredictNet MAE : 0.869683
Min PredictNet MAPE : 1.134682
Exceeds 68% Confidence Probability: 13.252342%
Exceeds 95% Confidence Probability: 8.094882%
